<img src="https://i.gifer.com/9C4I.gif">

# GeoQueries

GeoQuery enables individuals and organizations of all skill levels to freely find and aggregate satellite, economic, health, conflict, and other spatial data into a single, simple-to-use file compatible with Microsoft Excel and other common software. Without writing custom scripts, GeoQuery users can quickly get massive amounts of measurement data (from surveys, satellites, etc.) at fully customizable geographic boundaries (administrative zones, environmentally protected areas, etc.) and timeframes.

<img src="https://miro.medium.com/max/960/1*nHaqPlPl9IF1sWKeYgImhQ.gif">

## Import the necessary libraries

In [1]:
from pymongo import MongoClient
import pandas as pd
import folium
from folium import Choropleth, Circle, Marker, Icon, Map
from folium.plugins import HeatMap, MarkerCluster
import requests
import json
from pymongo import GEOSPHERE

import src.limpieza_texto as lt
import src.visualizacion as vt


import operator


## Generate conection with Mongo

<img width= 300 src="https://cdn.dribbble.com/users/805609/screenshots/2909157/connection.gif">

We have to make the conection with `Mongo Server`the place where we have all the json informations with the location of the different places.

In [2]:
from pymongo import MongoClient
mongo = MongoClient("localhost:27017")
db = mongo.get_database("Proyecto")

We have to choose the correct `DataBase`.

In [3]:
mongo.list_database_names()

['Proyecto',
 'Quotes',
 'Species',
 'admin',
 'companies',
 'config',
 'final',
 'geo',
 'labflask',
 'local']

Now we are in the correct database, que have to take the differnt collections.

In [4]:
db.list_collection_names()

['schools',
 'hairdresser',
 'gdf',
 'vegans',
 'airport',
 'starbucks2',
 'Starbucks',
 'basketball',
 'Dataframe',
 'pubs',
 'prueba']

In [28]:
schools = db.get_collection("schools")
dog = db.get_collection("hairdresser")
starbucks = db.get_collection("Starbucks")
vegan = db.get_collection("vegans")
airport = db.get_collection("airport")
basket = db.get_collection("basketball")
pubs = db.get_collection("pubs")

In [6]:
basket

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'Proyecto'), 'basketball')

In [7]:
data = pd.read_csv("data/nearby.csv")

In [8]:
data.head()

Unnamed: 0                                               name  \
0           0                                 Mission Kids Co-op   
1           1                   University Tutor - San Francisco   
2           2  La Scuola Internazionale Di San Francisco - Mi...   
3           3                              Erwan Davon Teachings   
4           4                                 Adventures In Clay   

                                            location    type    latitud  \
0  {'type': 'Point', 'coordinates': [37.756418550...  school  37.756419   
1  {'type': 'Point', 'coordinates': [37.757592, -...  school  37.757592   
2  {'type': 'Point', 'coordinates': [37.762145996...  school  37.762146   
3  {'type': 'Point', 'coordinates': [37.75723075,...  school  37.757231   
4  {'type': 'Point', 'coordinates': [37.762932722...  school  37.762933   

     longitud  
0 -122.417202  
1 -122.413628  
2 -122.416252  
3 -122.412394  
4 -122.415493

## Let´s start with geoqueries

<img src="https://media4.giphy.com/media/S5yqNNTQlEZfqQ7InC/200.gif">

There is a function in geoqueries called `Near` that help us to find the elements in a desired range from the place where we are looking for, sorted by distance.

Max distance from the searching point in meters.

First of all we have to set a orogin point to start the search

In [9]:
san_francisco = [-122.42046743548889, 37.77203444922543]
coord_point = {"type":"Point", "coordinates": san_francisco}
coord_point

{'type': 'Point', 'coordinates': [-122.42046743548889, 37.77203444922543]}

### Is there any `School` closer than 1,5 km?

In [22]:
vt.query_dist(schools, 1500)

_id  \
0  607c71678c69fb1e4cbd3d03   
1  607c71678c69fb1e4cbd3d01   
2  607c71678c69fb1e4cbd3d05   
3  607c71678c69fb1e4cbd3d07   
4  607c71678c69fb1e4cbd3d00   
5  607c71678c69fb1e4cbd3cfe   
6  607c71678c69fb1e4cbd3d0a   

                                                name  \
0                                 Hackbright Academy   
1                                     Interview Cake   
2                                  the cocktail camp   
3                              Children's Day School   
4                                 Adventures In Clay   
5  La Scuola Internazionale Di San Francisco - Mi...   
6                          San Francisco Brightworks   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.4193721...  
1  {'type': 'Point', 'coordinates': [-122.4189605...  
2  {'type': 'Point', 'coordinates': [-122.417919,...  
3  {'type': 'Point', 'coordinates': [-122.4250882...  
4  {'type': 'Point', 'coordinates': [-122.4154933...  
5  {'type': 'Point', 'coordinates': [-122.4162521...  
6  {'type': 'Point', 'coordinates': [-122.4104726...

### can we take dobby to the `pet shop` in less than 500 m?

In [24]:
vt.query_dist(dog, 500)

_id                     name  \
0  607c712f8c69fb1e4cbd3cdd  Embarkadero Social Club   
1  607c712f8c69fb1e4cbd3cd7    VCA All Pets Hospital   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.420359,...  
1  {'type': 'Point', 'coordinates': [-122.41752, ...

### is there any `Vegan Restaurant` for the CEO closer than 1 km?

In [31]:
vt.query_dist(vegan, 1000)

_id  \
0  607c71848c69fb1e4cbd3d15   
1  607c71848c69fb1e4cbd3d0c   
2  607c71848c69fb1e4cbd3d0d   

                                                name  \
0  Optometrists - Irene Koga, O.D. & Jennifer Jun...   
1                     Louise M. Davies Symphony Hall   
2                                         K&D Market   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.4190986...  
1  {'type': 'Point', 'coordinates': [-122.4201569...  
2  {'type': 'Point', 'coordinates': [-122.4236672...

### is the `airport` closer than 10 km?

In [32]:
vt.query_dist(airport, 10000)

_id                                           name  \
0  607c638e8c69fb1e4cbd3ccb                                        Gate 10   
1  607c638e8c69fb1e4cbd3cce                          Airport Super Shuttle   
2  607c638e8c69fb1e4cbd3ccc                            SFO Airport Mailers   
3  607c638e8c69fb1e4cbd3ccd  GOGO JETS - San Francisco Private Jet Charter   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.423949,...  
1  {'type': 'Point', 'coordinates': [-122.404844,...  
2  {'type': 'Point', 'coordinates': [-122.3961890...  
3  {'type': 'Point', 'coordinates': [-122.3979440...

### How many `starbucks` are in 1 km far?

In [17]:
vt.query_dist(starbucks, 1000)

_id       name  \
0  607d374e2153f55ca8be0903  Starbucks   
1  607d374e2153f55ca8be0900  Starbucks   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.4172976...  
1  {'type': 'Point', 'coordinates': [-122.428353,...

### is the `basketball` stadium closer than 5 km?

In [12]:
vt.query_dist(basket, 5000)

_id                              name  \
0  607c71158c69fb1e4cbd3cd0  Google Cloud Courtside Lounge 25   
1  607c71158c69fb1e4cbd3ccf                      Chase Center   
2  607c71158c69fb1e4cbd3cd2                       United Club   
3  607c71158c69fb1e4cbd3cd1                    Kezar Pavilion   

                                            location  
0  {'type': 'Point', 'coordinates': [-122.38773, ...  
1  {'type': 'Point', 'coordinates': [-122.387463,...  
2  {'type': 'Point', 'coordinates': [-122.387302,...  
3  {'type': 'Point', 'coordinates': [-122.4538689...

### How many `Pubs` are closer than 1 km?

In [35]:
vt.query_dist(pubs, 1000)

_id                       name  \
0   607c71518c69fb1e4cbd3cef  Brick & Mortar Music Hall   
1   607c71518c69fb1e4cbd3cf5               Public Works   
2   607c71518c69fb1e4cbd3cf3                   SF Oasis   
3   607c71518c69fb1e4cbd3cf7               The Holy COW   
4   607c71518c69fb1e4cbd3cee                   calle 11   
5   607c71518c69fb1e4cbd3ce9                    Halcyon   
6   607c71518c69fb1e4cbd3cfa            Paradise Lounge   
7   607c71518c69fb1e4cbd3ceb            Audio Nightclub   
8   607c71518c69fb1e4cbd3ce7       Bootie San Francisco   
9   607c71518c69fb1e4cbd3cf0                Skylark Bar   
10  607c71518c69fb1e4cbd3cf9                   Delirium   
11  607c71518c69fb1e4cbd3ce4               Double Dutch   
12  607c71518c69fb1e4cbd3ce1                   Jolene’s   

                                             location  
0   {'type': 'Point', 'coordinates': [-122.4201808...  
1   {'type': 'Point', 'coordinates': [-122.4193905...  
2   {'type': 'Point', 'coordinates': [-122.4144323...  
3   {'type': 'Point', 'coordinates': [-122.4143644...  
4   {'type': 'Point', 'coordinates': [-122.414017,...  
5   {'type': 'Point', 'coordinates': [-122.4139049...  
6   {'type': 'Point', 'coordinates': [-122.4138414...  
7   {'type': 'Point', 'coordinates': [-122.4138318...  
8   {'type': 'Point', 'coordinates': [-122.4128309...  
9   {'type': 'Point', 'coordinates': [-122.4216011...  
10  {'type': 'Point', 'coordinates': [-122.4228627...  
11  {'type': 'Point', 'coordinates': [-122.4238705...  
12  {'type': 'Point', 'coordinates': [-122.4132346...

In [ ]:
query = [{
    "$geoNear": {'near': [lon, lat],
                 'distanceField': 'distance',
                 'maxDistance': 2,
                 'spherical'  : True}}]

In [63]:
basket.aggregate([
   {
        "$geoNear" : {
        "near" : { type: "Point", "coordinates": [-122.42046743548889, 37.77203444922543] },
        "distanceField" : "dist.calculated",
        "maxDistance" : 2,
        "query" : { "category": "Parks" },
        "includeLocs": "dist.location",
        "spherical" : true
     }
   }
])

NameError: name 'category' is not defined

In [9]:
metros = 10000

In [10]:
cond_b = {"location": {"$near": {"$geometry": coord_point, "$maxDistance": 100000}}}

## GeoLocation with `Folium`

<img src="https://media1.tenor.com/images/8e1ca004043b8c59421e0da43bbc43fc/tenor.gif?itemid=4652942">

I am going to create a map showing the different types of business with a characteristic logo that allows us to distinguish them and to know which is the best area for our companies, in a visual way.

In [11]:
san_f = folium.Map(location = san_francisco, zoom_start = 14)
san_f2 = folium.Map(location = san_francisco, zoom_start = 14)

In [12]:
for i,row in data.iterrows():
    dicc = {
        "location" : [row["latitud"], row["longitud"]],
        "tooltip" : row["name"]        
    }
    
    if row["type"] == "school":
        
        icono = Icon(color = "blue",
                   prefix = "fa",
                   icon = "graduation-cap",
                   icon_color = "white"
                   )
        #Marker(**dicc, icon = icono).add_to(san_f)
        
    elif row["type"] == "dog_hairdresser":
        
        icono = Icon(color = "black",
                   prefix = "fa",
                   icon = "paw",
                   icon_color = "white"
                   ) 
        #Marker(**dicc, icon = icono).add_to(san_f)
        
    elif row["type"] == "starbucks":
        
        icono = folium.features.CustomIcon("./Images/starbucks.png")       
        #Marker(**dicc, icon = icono).add_to(san_f)
        
    elif row["type"] == "vegan_restaurant":
        
        icono = folium.features.CustomIcon("./Images/vegan.png")
        #Marker(**dicc, icon = icono).add_to(san_f)
        
    elif row["type"] == "airport":
        
        icono = Icon(color = "white",
                   prefix = "fa",
                   icon = "plane",
                   icon_color = "black"
                   )    
        #Marker(**dicc, icon = icono).add_to(san_f)

    elif row["type"] == "basket":
        
        icono = folium.features.CustomIcon("./Images/basket.png")
        #Marker(**dicc, icon = icono).add_to(san_f)
        
    elif row["type"] == "pub":
        
        icono = Icon(color = "pink",
                   prefix = "fa",
                   icon = "glass",
                   icon_color = "white"
                   )
        
    
    Marker(**dicc, icon = icono).add_to(san_f)
   

In [13]:
san_f

## HeatMap

<img src="https://aws1.discourse-cdn.com/business6/uploads/nodered/original/2X/a/adf075783516b42d509db71eaa06706cbf9b09d4.gif">

Heat maps are a type of visualisation in which the higher the concentration of a desired element, the more red it appears.

First of all, we have to select the different types of information in the dataframe.

In [14]:
data.type.unique()

array(['school', 'dog_hairdresser', 'starbucks', 'vegan_restaurant',
       'airport', 'basket', 'pub'], dtype=object)

I create a function where I enter the parameters and add a layer to the heatmap for each value in the requirement type list.

In [15]:
def heat_map(columna, dat, nombre_grupo, nombre_capa, mapa):
    df = dat[dat.type == columna]
    nombre_grupo = folium.FeatureGroup(name = nombre_capa)
    HeatMap(data= df[["latitud","longitud"]], radius = 15).add_to(nombre_grupo)
    nombre_grupo.add_to(san_f2)

In [16]:
vt.heat_map("school", data, "school_gr", "school", san_f2)
vt.heat_map("dog_hairdresser", data, "dog_gr", "Dog", san_f2)
vt.heat_map("starbucks", data, "str_gr", "Starbucks", san_f2)
vt.heat_map("vegan_restaurant", data, "vegan_gr", "Vegan", san_f2)
vt.heat_map("airport", data, "air_gr", "Airport", san_f2)
vt.heat_map("basket", data, "bsk_gr", "Basket", san_f2)
vt.heat_map("pub", data, "pub_gr", "Pub", san_f2)

Now I have to create de `layer control` to select or unselect the desired layers.

In [17]:
folium.LayerControl(collapsed=False).add_to(san_f2)

In [18]:
san_f2

# Conclusion

### As we can see, the best location for our company is in the centre of `San Francisco` as all requirements are met there. 

* There are many `schools` in the surrounding area.
* There are many `Starbucks` in the area waiting for executives.
* If Account managers need to travel, `San Francisco International Airport` is !!! km far from there.
* There are almost as many `pubs` in the vicinity as there are employees in the company.
* There are many `vegan` restaurants.
* In order to keep the maintenance staff happy, the `basketball stadium` is only a kilometre away.
* On the map you can also find all the `veterinary centres` so that dobby is always comfortable.

